* Tareas finde
- revisar datos fichero
- EDA fichero (datos faltantes, nulos, outliers)
- revisar web a scrapear
- revisar API

asignar a cada nombre unico un ID de hotel (estan mal asignados)
las estrellas se deben calcular con la media (ponerlo en el df de cuando se vaya a subir)
cambiar los IDs de cliente, generando id por cada email registrado

In [1]:
import pandas as pd
import requests
import numpy as np
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException, NoSuchElementException
from datetime import datetime
from datetime import date
from dotenv import load_dotenv
import os
from src import convertir_fecha, convertir_fechaeventos, scrapear_hoteles, extraccion_api, insertar_datos_automatico, conexion_postgres
import psycopg2

In [2]:
load_dotenv()

True

In [8]:
df = pd.read_parquet("../datos/reservas_hoteles.parquet", engine='fastparquet')

In [9]:
dfcopia = df.copy()

* duplicados

In [10]:
dfcopia = dfcopia.drop_duplicates()

In [11]:
hoteles_unicos = dfcopia.groupby('nombre_hotel')['id_hotel'].unique().reset_index()
hoteles_unicos

nombre_hotel                                           id_hotel
0                           [113, 194, 131, 114, 103, 181, 128, 186, 135, ...
1        Gran Hotel Madrid  [47, 6, 13, 15, 35, 14, 49, 28, 48, 38, 40, 43...
2     Hotel Brisas del Mar  [38, 28, 36, 49, 29, 35, 6, 14, 47, 33, 27, 43...
3     Hotel Camino del Sol  [35, 47, 13, 15, 48, 40, 19, 49, 33, 28, 27, 3...
4         Hotel Costa Azul  [40, 48, 38, 13, 15, 19, 28, 49, 36, 27, 14, 2...
5       Hotel Encanto Real  [43, 28, 35, 14, 47, 6, 38, 33, 36, 19, 3, 15,...
6   Hotel Jardines del Rey  [3, 33, 2, 35, 47, 49, 15, 36, 29, 38, 43, 13,...
7      Hotel Las Estrellas  [29, 28, 40, 47, 6, 14, 49, 13, 36, 48, 35, 38...
8      Hotel Los Almendros  [28, 3, 35, 49, 43, 29, 36, 33, 47, 6, 14, 15,...
9      Hotel Luz de Madrid  [13, 2, 36, 15, 27, 47, 35, 33, 38, 40, 49, 14...
10    Hotel Maravilla Real  [40, 28, 49, 48, 14, 38, 29, 15, 6, 19, 2, 35,...
11      Hotel Mirador Real  [3, 14, 47, 15, 28, 43, 33, 36, 29, 49, 6, 2, ...
12       Hotel Monte Verde  [14, 29, 40, 13, 6, 15, 33, 43, 38, 36, 19, 28...
13  Hotel Palacio Imperial  [27, 36, 2, 13, 43, 40, 15, 19, 35, 14, 47, 28...
14  Hotel Puerta del Cielo  [36, 40, 43, 13, 38, 6, 47, 27, 48, 35, 3, 49,...
15     Hotel Rincón Sereno  [6, 3, 49, 2, 48, 13, 28, 33, 14, 35, 47, 36, ...
16        Hotel Sol y Luna  [29, 19, 47, 15, 27, 36, 40, 14, 2, 28, 35, 13...
17      Hotel Torre Dorada  [14, 29, 36, 48, 40, 2, 13, 47, 35, 6, 3, 38, ...
18      Hotel Vista Alegre  [29, 2, 38, 48, 27, 47, 35, 49, 3, 28, 33, 14,...
19         Palacio del Sol  [6, 13, 14, 35, 28, 15, 19, 36, 47, 38, 29, 2,...

In [12]:
diccionario_hoteles = {"hotel": [], "id": []}
contador = 0
for hotel in hoteles_unicos["nombre_hotel"]:
    if hotel == "":
        pass
    else:
        diccionario_hoteles["hotel"].append(hotel)
        contador = contador + 1
        diccionario_hoteles["id"].append(contador)
df_dichoteles = pd.DataFrame(diccionario_hoteles)

In [13]:
mapa_hoteles = dict(zip(df_dichoteles["hotel"], df_dichoteles["id"]))

In [14]:
dfcopia["id_hotel"] = dfcopia["nombre_hotel"].map(mapa_hoteles).fillna(df["id_hotel"])

In [15]:
dfcopia["id_hotel"] = dfcopia["id_hotel"].astype(int)

In [16]:
dfcopia["id_hotel"].dtypes

dtype('int64')

In [17]:
hoteles_unicos = dfcopia.groupby('nombre_hotel')['id_hotel'].unique().reset_index()
hoteles_unicos

nombre_hotel                                           id_hotel
0                           [113, 194, 131, 114, 103, 181, 128, 186, 135, ...
1        Gran Hotel Madrid                                                [1]
2     Hotel Brisas del Mar                                                [2]
3     Hotel Camino del Sol                                                [3]
4         Hotel Costa Azul                                                [4]
5       Hotel Encanto Real                                                [5]
6   Hotel Jardines del Rey                                                [6]
7      Hotel Las Estrellas                                                [7]
8      Hotel Los Almendros                                                [8]
9      Hotel Luz de Madrid                                                [9]
10    Hotel Maravilla Real                                               [10]
11      Hotel Mirador Real                                               [11]
12       Hotel Monte Verde                                               [12]
13  Hotel Palacio Imperial                                               [13]
14  Hotel Puerta del Cielo                                               [14]
15     Hotel Rincón Sereno                                               [15]
16        Hotel Sol y Luna                                               [16]
17      Hotel Torre Dorada                                               [17]
18      Hotel Vista Alegre                                               [18]
19         Palacio del Sol                                               [19]

* poner id unico de cliente por cada mail

In [18]:
dfcopia["mail"].nunique()

14905

In [19]:
dfcopia["id_cliente"].nunique()

14847

In [20]:
dfcopia["id_cliente"]

0        346f2a77-33f4-4b2d-82f3-e8501e21b28d
1        346f2a77-33f4-4b2d-82f3-e8501e21b28d
2        6ec4d7d2-e382-47cc-94f6-c647577d4035
3        aed17fe8-eb18-4f69-bf08-df1afdc339c3
4        710a2fbb-264f-426a-aa66-f8fffd146a2d
                         ...                 
14995    de729428-ec23-4665-a5c9-79e3ec282470
14996    8469b819-d96a-4904-9cdd-710764f6301f
14997    e89751f4-3621-4636-81d3-90e2baa709cb
14998    c4117358-fd89-44cd-b388-4ec6d3538c72
14999    f97ec0a6-6fb7-401e-83fa-5fb3957ee02b
Name: id_cliente, Length: 15000, dtype: object

In [21]:
lista_mails = dfcopia["mail"].unique().tolist()
lista_idmails = []
contador = 0
for mail in lista_mails:
    contador = contador + 1
    lista_idmails.append(contador)
diccionario_mails = dict(zip(lista_mails, lista_idmails))
dfcopia["id_cliente"] = dfcopia["mail"].map(diccionario_mails)

* nulos

In [22]:
def calcular_nulos(dfcopia):
    """Calcula la cantidad de valores nulos en cada columna de un DataFrame."""
    nulos = dfcopia.isnull().sum()  # Suma los nulos por columna
    porcentaje_nulos = (nulos / len(dfcopia)) * 100  # Calcula el porcentaje de nulos
    resultados = pd.DataFrame({
        'Cantidad de Nulos': nulos,
        'Porcentaje de Nulos': porcentaje_nulos.round(2)
    })
    return resultados

In [23]:
resultado_nulos = calcular_nulos(dfcopia)
resultado_nulos

Cantidad de Nulos  Porcentaje de Nulos
id_reserva                       0                 0.00
id_cliente                       0                 0.00
nombre                           0                 0.00
apellido                         0                 0.00
mail                             0                 0.00
competencia                      0                 0.00
fecha_reserva                    0                 0.00
inicio_estancia                 75                 0.50
final_estancia                  75                 0.50
id_hotel                         0                 0.00
precio_noche                  5224                34.83
nombre_hotel                     0                 0.00
estrellas                     5172                34.48
ciudad                           0                 0.00

In [24]:
dfcopia["inicio_estancia"] = dfcopia["inicio_estancia"].fillna("2025-03-01")

In [25]:
dfcopia["final_estancia"] = dfcopia["final_estancia"].fillna("2025-03-02")

In [26]:
medias = dfcopia.groupby("id_hotel")["precio_noche"].mean().round(2)
medias = pd.DataFrame(medias).reset_index()

In [27]:
diccionario_medias = dict(zip(medias["id_hotel"], medias["precio_noche"]))

In [28]:
dfcopia['precio_noche'] = dfcopia['precio_noche'].fillna(dfcopia['id_hotel'].map(diccionario_medias))

In [29]:
dfcopia["ciudad"] = "Madrid"

In [30]:
dfcopia["ciudad"].value_counts()

ciudad
Madrid    15000
Name: count, dtype: int64

In [31]:
dfcompetencia = dfcopia[dfcopia["competencia"] == True]

In [32]:
dfcompetencia["id_hotel"].unique().tolist()

[113, 194, 131, 114, 103, 181, 128, 186, 135, 117]

* outliers

In [33]:
def detectar_outliers_iqr(df):
    """Calcula la cantidad y porcentaje de outliers en cada columna numérica de un DataFrame usando el método IQR."""
    resultados = {}

    for col in df.select_dtypes(include=['number']).columns:  # Solo columnas numéricas
        Q1 = df[col].quantile(0.25)  # Primer cuartil
        Q3 = df[col].quantile(0.75)  # Tercer cuartil
        IQR = Q3 - Q1  # Rango Intercuartil

        # Definir los límites de los outliers
        lower_bound = Q1 - 1.5 * IQR
        upper_bound = Q3 + 1.5 * IQR

        # Filtrar los valores outliers
        outliers = df[(df[col] < lower_bound) | (df[col] > upper_bound)]
        num_outliers = len(outliers)
        total_values = len(df)
        percentage_outliers = (num_outliers / total_values) * 100

        # Guardar resultados
        resultados[col] = {
            'Cantidad de Outliers': num_outliers,
            'Porcentaje de Outliers': round(percentage_outliers, 2)
        }

    return pd.DataFrame(resultados).T  # Convertir resultados en DataFrame

In [34]:
resultado_outliers = detectar_outliers_iqr(dfcopia)
resultado_outliers

Cantidad de Outliers  Porcentaje de Outliers
id_cliente                     0.0                     0.0
id_hotel                       0.0                     0.0
precio_noche                   0.0                     0.0
estrellas                      0.0                     0.0

* Webscrapping

* scrapear precio nombre y estrellas

In [35]:
url_base = "https://all.accor.com/ssr/app/ibis/hotels/madrid-spain/index.es.shtml?compositions=1&stayplus=false&snu=false&hideWDR=false&accessibleRooms=false&hideHotelDetails=false&dateIn=2025-03-01&nights=1&destination=madrid-spain"

In [36]:
def scrapear_hoteles (url_base, dict):
    if "nombre_hotel" not in dict:
        dict["nombre_hotel"] = []
    if "valoraciones" not in dict:
        dict["valoraciones"] = []
    if "precio" not in dict:
        dict["precio"] = []
    if "fecha" not in dict:
        dict["fecha"] = []
    service = Service(ChromeDriverManager().install())
    options = Options()
    options.add_argument("--start-maximized")
    driver = webdriver.Chrome(service=service, options=options)
    driver.get(url_base)
    cookie_button = driver.find_element(By.XPATH, "//button[contains(text(), 'Accept')]")
    cookie_button2 = driver.find_element(By.XPATH, "//button[contains(text(), 'A')]")
    try:
        cookie_button.click()
    except:
        cookie_button2.click()
    wait = WebDriverWait(driver, 10)
    wait.until(EC.presence_of_all_elements_located((By.CSS_SELECTOR, "span.booking-price__number.mcp-price-number")))
    info = driver.find_elements(By.CSS_SELECTOR, ".hotelblock__content")
    for item in info:
        precio = item.find_element(By.CSS_SELECTOR, "span.booking-price__number.mcp-price-number").text
        nombre = item.find_element(By.CSS_SELECTOR, ".title__link").text
        nombre_hotel1 = nombre
        nombre_hotel1 = nombre_hotel1.split()
        nombre_hotel = " ".join(nombre_hotel1[:-2])
        valoraciones = item.find_element(By.CSS_SELECTOR, ".ratings__score").text
        valoraciones1 = valoraciones.split("/")[0]
        fecha = datetime.now()
        fecha = fecha.strftime("%Y-%m-%d")
        dict["nombre_hotel"].append(nombre_hotel)
        dict["valoraciones"].append(valoraciones1)
        dict["precio"].append(precio)
        dict["fecha"].append(fecha)
    dfscrap = pd.DataFrame(dict)
    dfscrap.to_csv("../datos/datos_webscrapping.csv", index=False)
    driver.quit()

In [37]:
dictio_scrap = {}
scrapear_hoteles(url_base, dictio_scrap)

In [38]:
dfscrap = pd.DataFrame(dictio_scrap)

In [39]:
dictio_mergeo = dict(zip(dfscrap["nombre_hotel"], dfcompetencia["id_hotel"].unique().tolist()))

In [40]:
dfscrap["id_hotel"] = dfscrap["nombre_hotel"].map(dictio_mergeo)

In [41]:
dfscrap.columns

Index(['nombre_hotel', 'valoraciones', 'precio', 'fecha', 'id_hotel'], dtype='object')

In [42]:
dfcompetencia.columns

Index(['id_reserva', 'id_cliente', 'nombre', 'apellido', 'mail', 'competencia',
       'fecha_reserva', 'inicio_estancia', 'final_estancia', 'id_hotel',
       'precio_noche', 'nombre_hotel', 'estrellas', 'ciudad'],
      dtype='object')

In [43]:
dfcompetencia_mergeado = dfcompetencia.merge(dfscrap, on="id_hotel")

In [44]:
dfcompetencia_mergeado["fecha_reserva"] = dfcompetencia_mergeado["fecha"]

In [45]:
dfcompetencia_mergeado["precio_noche"] = dfcompetencia_mergeado["precio"]

In [46]:
dfcompetencia_mergeado["nombre_hotel_x"] = dfcompetencia_mergeado["nombre_hotel_y"]

In [47]:
dfcompetencia_mergeado = dfcompetencia_mergeado.drop(columns= ["nombre_hotel_y", "precio","fecha", "estrellas"])

In [48]:
dfcompetencia_mergeado = dfcompetencia_mergeado.rename(columns={"nombre_hotel_x":"nombre_hotel", "valoraciones": "estrellas"})

In [49]:
dfcompetencia_mergeado

id_reserva  id_cliente          nombre  \
0     5256cc90-139b-43d2-8ec5-412495d751cf           1       Feliciana   
1     84fd6209-bd8d-4a92-bfe6-c68ee2c49271           2        Leonardo   
2     4d65096e-5f12-4ce7-9fd6-dd20e3cf5194           8          Judith   
3     458029ad-cc9b-4d85-8290-fec170bcc02d          10          Adolfo   
4     ac0fe86e-90a0-4fe6-a02e-6ea00e9a8621          12    María Carmen   
...                                    ...         ...             ...   
5167  e856adee-838c-4031-920c-05ec5f1e32e6       14895          Jesusa   
5168  77134049-6e4f-49b0-a6f8-93b7466b1c22       14897            Cruz   
5169  19aef6f3-3e85-4719-9dff-b768d9bfe5a9       14899  Jose Francisco   
5170  aa092c3e-7fe6-4985-a5a8-cacd38554b1b       14902            Toño   
5171  6d1f590c-ae87-4582-bc99-9b8cbf1d8e28       14904        Custodia   

      apellido                               mail  competencia fecha_reserva  \
0       Cantón       feliciana.cantón@example.com         True    2025-02-24   
1       Hierro        leonardo.hierro@example.com         True    2025-02-24   
2        Rivas           judith.rivas@example.com         True    2025-02-24   
3       Cuervo          adolfo.cuervo@example.com         True    2025-02-24   
4      Navarro   maría carmen.navarro@example.com         True    2025-02-24   
...        ...                                ...          ...           ...   
5167  Espinosa        jesusa.espinosa@example.com         True    2025-02-24   
5168   Hurtado           cruz.hurtado@example.com         True    2025-02-24   
5169    Cortes  jose francisco.cortes@example.com         True    2025-02-24   
5170   Narváez           toño.narváez@example.com         True    2025-02-24   
5171     Marco         custodia.marco@example.com         True    2025-02-24   

     inicio_estancia final_estancia  id_hotel precio_noche  \
0         2025-03-01     2025-03-02       113          110   
1         2025-03-01     2025-03-02       194          119   
2         2025-03-01     2025-03-02       131          119   
3         2025-03-01     2025-03-02       114          107   
4         2025-03-01     2025-03-02       103          116   
...              ...            ...       ...          ...   
5167      2025-03-01     2025-03-02       135           99   
5168      2025-03-01     2025-03-02       128          102   
5169      2025-03-01     2025-03-02       186           83   
5170      2025-03-01     2025-03-02       114          107   
5171      2025-03-01     2025-03-02       194          119   

                              nombre_hotel  ciudad estrellas  
0              ibis budget Madrid Calle 30  Madrid       4.4  
1     ibis budget Madrid Centro las Ventas  Madrid       4.3  
2                 ibis Madrid Calle Alcalá  Madrid       4.5  
3              ibis budget Madrid Vallecas  Madrid       4.3  
4           ibis Madrid Aeropuerto Barajas  Madrid       4.4  
...                                    ...     ...       ...  
5167             ibis budget Madrid Getafe  Madrid       4.2  
5168         ibis budget Madrid Aeropuerto  Madrid         4  
5169                ibis Madrid Alcobendas  Madrid       4.4  
5170           ibis budget Madrid Vallecas  Madrid       4.3  
5171  ibis budget Madrid Centro las Ventas  Madrid       4.3  

[5172 rows x 14 columns]

* API

In [50]:
url = "https://datos.madrid.es/egob/catalogo/300107-0-agenda-actividades-eventos.json"

In [51]:
def extraccion_api(url):
    response = requests.get(url)
    if response.status_code == 200:
        data = response.json() # Convertir la respuesta a un diccionario de Python
        print(data)
    else:
        print(f"Error en la solicitud: {response.status_code}")
    eventos = data["@graph"]
    lista_eventos = []
    for evento in eventos:
        lista_eventos.append(evento)
    dfapi = pd.DataFrame(eventos)
    return dfapi


In [52]:
extraccion_api(url)

{'@context': {'c': 'http://www.w3.org/2002/12/cal#', 'dcterms': 'http://purl.org/dc/terms/', 'geo': 'http://www.w3.org/2003/01/geo/wgs84_pos#', 'loc': 'http://purl.org/ctic/infraestructuras/localizacion#', 'org': 'http://purl.org/ctic/infraestructuras/organizacion#', 'vcard': 'http://www.w3.org/2006/vcard/ns#', 'schema': 'https://schema.org/', 'title': 'vcard:fn', 'id': 'dcterms:identifier', 'relation': 'dcterms:relation', 'references': 'dcterms:references', 'address': 'vcard:adr', 'area': 'loc:barrio', 'district': 'loc:distrito', 'locality': 'vcard:locality', 'postal-code': 'vcard:postal-code', 'street-address': 'vcard:street-address', 'location': 'vcard:geo', 'latitude': 'geo:lat', 'longitude': 'geo:long', 'organization': 'vcard:org', 'organization-desc': 'dcterms:description', 'accesibility': 'org:accesibilidad', 'services': 'org:servicios', 'schedule': 'org:horario', 'organization-name': 'vcard:organization-name', 'description': 'c:summary', 'link': 'c:url', 'uid': 'c:uid', 'dtstar

@id  \
0     https://datos.madrid.es/egob/catalogo/tipo/eve...   
1     https://datos.madrid.es/egob/catalogo/tipo/eve...   
2     https://datos.madrid.es/egob/catalogo/tipo/eve...   
3     https://datos.madrid.es/egob/catalogo/tipo/eve...   
4     https://datos.madrid.es/egob/catalogo/tipo/eve...   
...                                                 ...   
1144  https://datos.madrid.es/egob/catalogo/tipo/eve...   
1145  https://datos.madrid.es/egob/catalogo/tipo/eve...   
1146  https://datos.madrid.es/egob/catalogo/tipo/eve...   
1147  https://datos.madrid.es/egob/catalogo/tipo/eve...   
1148  https://datos.madrid.es/egob/catalogo/tipo/eve...   

                                                  @type        id  \
0     https://datos.madrid.es/egob/kos/actividades/E...  12677513   
1     https://datos.madrid.es/egob/kos/actividades/P...  12651622   
2     https://datos.madrid.es/egob/kos/actividades/E...  12693864   
3     https://datos.madrid.es/egob/kos/actividades/T...  12691220   
4                                                   NaN  12534372   
...                                                 ...       ...   
1144  https://datos.madrid.es/egob/kos/actividades/P...  12513905   
1145  https://datos.madrid.es/egob/kos/actividades/1...  12675318   
1146  https://datos.madrid.es/egob/kos/actividades/E...  12621974   
1147  https://datos.madrid.es/egob/kos/actividades/R...  12696640   
1148  https://datos.madrid.es/egob/kos/actividades/P...  12513909   

                                                  title  \
0               25º aniversario de la revista La Fragua   
1                                               3CLONWS   
2          60 Premio Reina Sofía de Pintura y Escultura   
3                                       7 pares de pies   
4                                           A toda vela   
...                                                 ...   
1144  «Secretos de belleza (interior): amistad, ritu...   
1145                      ¿Café o GinTonic? - Moratalaz   
1146                             ¿Hay vida en el metro?   
1147                         ¿Qué sueñan los príncipes?   
1148                      Ça Marche 'Trabajos forzados'   

                                            description  free  \
0                                                           1   
1     Un espectáculo que comienza con cajas improvis...     0   
2                                                           1   
3     Artista Y.    Recomendada para todos los públi...     1   
4                                                           0   
...                                                 ...   ...   
1144                                                        0   
1145                               Duración: 90 minutos     1   
1146  Mónica Salgado y José V. Pinedo  Sinopsis: En ...     1   
1147  Cía. Tábula rasa producciones  TEATRO – POESÍA...     1   
1148                                                        0   

                                                  price  \
0                                                         
1                                                         
2                                                         
3                                                         
4     8 euros por alumno (Grupos mínimo 20 alumnos)....   
...                                                 ...   
1144  Descarga gratuita de invitaciones una semana a...   
1145                                                      
1146                                                      
1147                                                      
1148                                           14 euros   

                    dtstart                  dtend   time  ...  \
0     2025-02-24 00:00:00.0  2025-03-02 23:59:00.0         ...   
1     2025-03-21 19:00:00.0  2025-03-22 23:59:00.0  19:00  ...   
2     2025-02-27 00:00:00.0  2025-03-23 23:59:00.0         ...   
3     2025-03-23 12:00:00.0  2025-03-23 23:59:00.0 

In [53]:
response = requests.get(url)
if response.status_code == 200:
    data = response.json() # Convertir la respuesta a un diccionario de Python
    print(data)
else:
    print(f"Error en la solicitud: {response.status_code}")
eventos = data["@graph"]
lista_eventos = []
for evento in eventos:
    lista_eventos.append(evento)
dfapi = pd.DataFrame(eventos)

{'@context': {'c': 'http://www.w3.org/2002/12/cal#', 'dcterms': 'http://purl.org/dc/terms/', 'geo': 'http://www.w3.org/2003/01/geo/wgs84_pos#', 'loc': 'http://purl.org/ctic/infraestructuras/localizacion#', 'org': 'http://purl.org/ctic/infraestructuras/organizacion#', 'vcard': 'http://www.w3.org/2006/vcard/ns#', 'schema': 'https://schema.org/', 'title': 'vcard:fn', 'id': 'dcterms:identifier', 'relation': 'dcterms:relation', 'references': 'dcterms:references', 'address': 'vcard:adr', 'area': 'loc:barrio', 'district': 'loc:distrito', 'locality': 'vcard:locality', 'postal-code': 'vcard:postal-code', 'street-address': 'vcard:street-address', 'location': 'vcard:geo', 'latitude': 'geo:lat', 'longitude': 'geo:long', 'organization': 'vcard:org', 'organization-desc': 'dcterms:description', 'accesibility': 'org:accesibilidad', 'services': 'org:servicios', 'schedule': 'org:horario', 'organization-name': 'vcard:organization-name', 'description': 'c:summary', 'link': 'c:url', 'uid': 'c:uid', 'dtstar

In [54]:
dfapi1 = dfapi[["id", "title", "link", "address", "time", "dtstart", "dtend", "organization"]]

In [55]:
def convertir_fecha(dataframe):
    for col in dataframe.filter(like="dt", axis=1):
        dataframe[col] = pd.to_datetime(dataframe[col]).dt.strftime('%Y-%m-%d')
    return dataframe

In [56]:
convertir_fecha(dfapi1)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\344019579.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe[col] = pd.to_datetime(dataframe[col]).dt.strftime('%Y-%m-%d')
C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\344019579.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe[col] = pd.to_datetime(dataframe[col]).dt.strftime('%Y-%m-%d')


id                                              title  \
0     12677513            25º aniversario de la revista La Fragua   
1     12651622                                            3CLONWS   
2     12693864       60 Premio Reina Sofía de Pintura y Escultura   
3     12691220                                    7 pares de pies   
4     12534372                                        A toda vela   
...        ...                                                ...   
1144  12513905  «Secretos de belleza (interior): amistad, ritu...   
1145  12675318                      ¿Café o GinTonic? - Moratalaz   
1146  12621974                             ¿Hay vida en el metro?   
1147  12696640                         ¿Qué sueñan los príncipes?   
1148  12513909                      Ça Marche 'Trabajos forzados'   

                                                   link  \
0     http://www.madrid.es/sites/v/index.jsp?vgnextc...   
1     http://www.madrid.es/sites/v/index.jsp?vgnextc...   
2     http://www.madrid.es/sites/v/index.jsp?vgnextc...   
3     http://www.madrid.es/sites/v/index.jsp?vgnextc...   
4     http://www.madrid.es/sites/v/index.jsp?vgnextc...   
...                                                 ...   
1144  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
1145  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
1146  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
1147  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
1148  http://www.madrid.es/sites/v/index.jsp?vgnextc...   

                                                address   time     dtstart  \
0     {'district': {'@id': 'https://datos.madrid.es/...         2025-02-24   
1     {'district': {'@id': 'https://datos.madrid.es/...  19:00  2025-03-21   
2     {'district': {'@id': 'https://datos.madrid.es/...         2025-02-27   
3     {'district': {'@id': 'https://datos.madrid.es/...  12:00  2025-03-23   
4     {'district': {'@id': 'https://datos.madrid.es/...         2024-10-01   
...                                                 ...    ...         ...   
1144  {'district': {'@id': 'https://datos.madrid.es/...         2025-04-29   
1145  {'district': {'@id': 'https://datos.madrid.es/...  19:00  2025-03-08   
1146  {'district': {'@id': 'https://datos.madrid.es/...         2024-12-16   
1147  {'district': {'@id': 'https://datos.madrid.es/...  19:00  2025-03-15   
1148  {'district': {'@id': 'https://datos.madrid.es/...  20:00  2025-05-07   

           dtend                                       organization  
0     2025-03-02  {'organization-name': 'Biblioteca Pública Muni...  
1     2025-03-22  {'organization-name': 'Teatro Circo Price', 'a...  
2     2025-03-23  {'organization-name': 'Centro Cultural Casa de...  
3     2025-03-23  {'organization-name': 'Centro Cultural Antonio...  
4     2025-06-01  {'organization-name': 'Matadero Madrid', 'acce...  
...          ...                                                ...  
1144  2025-04-29  {'organization-name': 'Centro de Cultura Conte...  
1145  2025-03-08  {'organization-name': 'Centro Cultural el Tori...  
1146  2025-02-27  {'organization-name': 'Centro Sociocultural Fr...  
1147  2025-03-15  {'organization-name': 'Centro Cultural la Elip...  
1148  2025-05-07  {'organization-name': 'Centro de Cultura Conte...  

[1149 rows x 8 columns]

In [57]:
dfapi1[dfapi1["id"] == "12682147"]

id                                   title  \
72  12682147  Baile de Carnaval. Concierto de Origen   

                                                 link address   time  \
72  http://www.madrid.es/sites/v/index.jsp?vgnextc...     NaN  19:30   

       dtstart       dtend organization  
72  2025-03-01  2025-03-01          NaN

In [58]:
dfapi1["address"][0]

{'district': {'@id': 'https://datos.madrid.es/egob/kos/Provincia/Madrid/Municipio/Madrid/Distrito/Centro'},
 'area': {'@id': 'https://datos.madrid.es/egob/kos/Provincia/Madrid/Municipio/Madrid/Distrito/Centro/Barrio/Palacio',
  'locality': 'MADRID',
  'postal-code': '28005',
  'street-address': 'CALLE SAN JUSTO 5'}}

In [59]:
dfapi1["organization"][0]

{'organization-name': 'Biblioteca Pública Municipal Iván de Vargas (Centro)',
 'accesibility': '1,6'}

In [60]:
dfapi1["address"].isnull().sum()

np.int64(108)

In [61]:
dfapifechas = dfapi1[(dfapi1["dtstart"] == "2025-03-01") | (dfapi1["dtend"] == "2025-03-02")]

In [62]:
dfapifechas["codigo-postal"] = dfapifechas["address"].apply(lambda x: x.get("area", {}).get("postal-code") if pd.notna(x) else "No Disponible")


C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\2043658518.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfapifechas["codigo-postal"] = dfapifechas["address"].apply(lambda x: x.get("area", {}).get("postal-code") if pd.notna(x) else "No Disponible")


In [63]:
dfapifechas["direccion"] = dfapifechas["address"].apply(lambda x: x.get("area", {}).get("street-address") if pd.notna(x) else "No Disponible")

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\1231952364.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfapifechas["direccion"] = dfapifechas["address"].apply(lambda x: x.get("area", {}).get("street-address") if pd.notna(x) else "No Disponible")


In [64]:
dfapifechas["organizacion"] = dfapifechas["organization"].apply(lambda x: x.get("organization-name", {})if pd.notna(x) else "No Disponible")

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\1980337032.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfapifechas["organizacion"] = dfapifechas["organization"].apply(lambda x: x.get("organization-name", {})if pd.notna(x) else "No Disponible")


In [65]:
dfapifechas.head()

id                                       title  \
0   12677513     25º aniversario de la revista La Fragua   
56  12682299    Asalto a la lectura. Tres cerditos y más   
60  12691299                       Atlantiques + Dahomey   
72  12682147      Baile de Carnaval. Concierto de Origen   
73  12682149  Baile de Carnaval. Concierto de Versioneta   

                                                 link  \
0   http://www.madrid.es/sites/v/index.jsp?vgnextc...   
56  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
60  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
72  http://www.madrid.es/sites/v/index.jsp?vgnextc...   
73  http://www.madrid.es/sites/v/index.jsp?vgnextc...   

                                              address   time     dtstart  \
0   {'district': {'@id': 'https://datos.madrid.es/...         2025-02-24   
56  {'district': {'@id': 'https://datos.madrid.es/...  11:00  2025-03-01   
60  {'district': {'@id': 'https://datos.madrid.es/...  19:30  2025-03-01   
72                                                NaN  19:30  2025-03-01   
73                                                NaN  21:15  2025-03-01   

         dtend                                       organization  \
0   2025-03-02  {'organization-name': 'Biblioteca Pública Muni...   
56  2025-03-01  {'organization-name': 'Centro Cultural Clara d...   
60  2025-03-01  {'organization-name': 'Cineteca Madrid', 'acce...   
72  2025-03-01                                                NaN   
73  2025-03-01                                                NaN   

    codigo-postal          direccion  \
0           28005  CALLE SAN JUSTO 5   
56          28015   CALLE AMANIEL 29   
60          28045    PLAZA LEGAZPI 8   
72  No Disponible      No Disponible   
73  No Disponible      No Disponible   

                                         organizacion  
0   Biblioteca Pública Municipal Iván de Vargas (C...  
56  Centro Cultural Clara del Rey - Museo ABC (Cen...  
60                                    Cineteca Madrid  
72                                      No Disponible  
73                                      No Disponible

In [66]:
dfapifechas.columns

Index(['id', 'title', 'link', 'address', 'time', 'dtstart', 'dtend',
       'organization', 'codigo-postal', 'direccion', 'organizacion'],
      dtype='object')

In [67]:
dfapifechaslimpio = dfapifechas.drop(columns = ["address", "organization"], axis = 1)

In [68]:
dfapifechaslimpio["time"] = dfapifechaslimpio["time"].replace('', "No Disponible")

In [69]:
dfapifechaslimpio

id                                              title  \
0     12677513            25º aniversario de la revista La Fragua   
56    12682299           Asalto a la lectura. Tres cerditos y más   
60    12691299                              Atlantiques + Dahomey   
72    12682147             Baile de Carnaval. Concierto de Origen   
73    12682149         Baile de Carnaval. Concierto de Versioneta   
94    12690573                                    Black sad women   
118   12694234  Carnaval en familia. Espectáculo familiar. Car...   
121   12691752                               Carnaval en Matadero   
132   12690602                                       Century Rock   
141   12693374                                          Chup-Chup   
161   12693191                                     Circo Homónimo   
215   12688786                              Concurso de disfraces   
216   12695974         Concurso de Disfraces y Baile con Orquesta   
217   12686562         Concurso de Disfraces y Baile con Orquesta   
237   12693385                               Coro Yelena Lafargue   
247   12690609                       Cuatro historias de alquiler   
263   12039151                    De Casa de Campo a Madrid Río I   
285   12688789          Desfile con charanga y taller de máscaras   
305   12691276                                       El arca rusa   
310   12685037                        El carnaval de los animales   
327   11725143                    El Retiro a través de la música   
376   12682155                   Exhibición de chirigotas adultos   
377   12682150                Exhibición de chirigotas infantiles   
394   12694176  Exposición de Pintura `Paisajes´ y `Rincones d...   
398   12537164   Exposición de pintura: 'Evelyn contemporary art'   
427   12683865     Fiesta de carnaval en el Barrio del Aeropuerto   
428   12683859  Fiesta de carnaval en el Barro de la Alameda d...   
463   11771304                                    Huerto familiar   
489   12233848           Itinerario Ornitológico Parque del Oeste   
490   12233828  Itinerario Ornitológico Parque Emperatriz Marí...   
495   12632975  Itinerario por el Parque Forestal de Valdebeba...   
533   12693346                             Julieta, pero no mucho   
556   12691223                            La gira de rock Quijote   
599   12690339             Las marionetas de la Dehesa te cuentan   
620   12518846                         Los gigantes de la montaña   
627   12693340                        Los secretos de los cuentos   
628   12234105        Los Secretos del Capricho: público familiar   
629   12687545                                      Los soñadores   
649   12696621                                            Macbeth   
660   12686179  Marconi. Pasacalles, Concurso de Disfraces y O...   
682   12691228                                           Memories   
684   12652164                   Mermelhada - El Retablo (Madrid)   
706   12690099                                             Murdle   
732   12661729                             Nosotras creamos mundo   
791   12694040                       Rastreando la vida silvestre   
808   12690635  Retrato de la Mujer en Ciencia:  ilustrando la...   
826   12686205  San Cristóbal de los Ángeles. Concurso de Disf...   
832   12694038  Senda Descubre la vida silvestre del parque de...   
834   12630477            Senderismo al invernadero de Arganzuela   
835   12690327  Senderismo urbano. Emilia Pardo Bazán: mujer e...   
850   12694451       Sobreviure a l'incendi: El documental de ZOO   
866   12696746  Taller de Bancal lasaña en el Huerto Urbano Co...   
904   12696701  Taller de semilleros en el Huerto Urbano Comun...   
920   12696013                               Talleres de máscaras   
926   12686923  Talleres Infantiles de Carnaval. Centros Socio...   
939   12693997                                   Tejiendo Colores   
989   12691324                                          Valerosas   
1010  1268

In [70]:
dfpropio = dfcopia[dfcopia["competencia"] == False]

In [71]:
dfpropio

id_reserva  id_cliente     nombre   apellido  \
2      40c4cb55-d1f5-407b-832f-4756b8ff77b4           3      Maite  Calatayud   
3      f2ce8df5-7844-43e1-8c0f-97ce7a208f21           4      Tecla      Bonet   
4      57d4515a-447d-4067-afcb-9bdcf4e4e915           5    Amílcar     Andrés   
5      ccbd9fe9-5a60-4f6f-bed3-73a7158ecba7           6       Joan    Vazquez   
6      99c3dc4f-663c-45f7-849a-ac9313f3746a           7      Chelo       Flor   
...                                     ...         ...        ...        ...   
14992  277edc09-64da-4a99-b6e2-395491a5f1a7       14898  Adoración   Cuadrado   
14994  0b1676e5-12a9-48cd-944d-b3d09e1ddf08       14900    Edgardo    Sanchez   
14995  58acd6f3-7160-4973-b951-b14188937444       14901     Lorena      Román   
14997  af0f6afa-e7d2-410a-8cdd-5eb62b1e4788       14903      Nadia    Verdugo   
14999  55b1c8de-bc13-4e4c-9dd7-50437788e361       14905    Brígida      Salom   

                                 mail  competencia fecha_reserva  \
2         maite.calatayud@example.com        False    2025-02-09   
3             tecla.bonet@example.com        False    2025-02-08   
4          amílcar.andrés@example.com        False    2025-02-02   
5            joan.vazquez@example.com        False    2025-02-08   
6              chelo.flor@example.com        False    2025-02-09   
...                               ...          ...           ...   
14992  adoración.cuadrado@example.com        False    2025-02-06   
14994     edgardo.sanchez@example.com        False    2025-02-06   
14995        lorena.román@example.com        False    2025-02-06   
14997       nadia.verdugo@example.com        False    2025-02-11   
14999       brígida.salom@example.com        False    2025-02-08   

      inicio_estancia final_estancia  id_hotel  precio_noche  \
2          2025-03-01     2025-03-02        12        119.96   
3          2025-03-01     2025-03-02         2        211.53   
4          2025-03-01     2025-03-02         3        378.37   
5          2025-03-01     2025-03-02        14         85.45   
6          2025-03-01     2025-03-02         5        309.80   
...               ...            ...       ...           ...   
14992      2025-03-01     2025-03-02         6        305.79   
14994      2025-03-01     2025-03-02        15        381.16   
14995      2025-03-01     2025-03-02         6        111.78   
14997      2025-03-01     2025-03-02         2        442.96   
14999      2025-03-01     2025-03-02        18        362.39   

                 nombre_hotel  estrellas  ciudad  
2           Hotel Monte Verde        1.0  Madrid  
3        Hotel Brisas del Mar        5.0  Madrid  
4        Hotel Camino del Sol        1.0  Madrid  
5      Hotel Puerta del Cielo        5.0  Madrid  
6          Hotel Encanto Real        1.0  Madrid  
...                       ...        ...     ...  
14992  Hotel Jardines del Rey        1.0  Madrid  
14994     Hotel Rincón Sereno        1.0  Madrid  
14995  Hotel Jardines del Rey        1.0  Madrid  
14997    Hotel Brisas del Mar        5.0  Madrid  
14999      Hotel Vista Alegre        5.0  Madrid  

[9828 rows x 14 columns]

In [72]:
medias_valoraciones = dfpropio.groupby("id_hotel")["estrellas"].mean().round(2).reset_index()

In [73]:
diccionario_valoraciones = dict(zip(medias_valoraciones["id_hotel"], medias_valoraciones["estrellas"]))

In [74]:
dfpropio["estrellas"] = dfpropio["id_hotel"].map(diccionario_valoraciones)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\1566015725.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfpropio["estrellas"] = dfpropio["id_hotel"].map(diccionario_valoraciones)


* Tabla ciudad

In [75]:
listaciudad = dfpropio["ciudad"].unique().tolist()
df_ciudad = pd.DataFrame(listaciudad, columns=["ciudad"])
df_ciudad["id_ciudad"] = 1

* Tabla eventos

In [76]:
dfapifechaslimpio["id_ciudad"] = 1

In [77]:
df_eventos = dfapifechaslimpio.copy()

In [78]:
df_eventos["id"] = range(1, len(df_eventos["id"]) + 1)

In [79]:
df_eventos.columns

Index(['id', 'title', 'link', 'time', 'dtstart', 'dtend', 'codigo-postal',
       'direccion', 'organizacion', 'id_ciudad'],
      dtype='object')

In [80]:
df_eventos = df_eventos.rename(columns={"id": "id_evento", "title":"nombre_evento", "link": "url_evento", "codigo-postal": "codigo_postal", "time": "horario", "dtstart": "fecha_inicio", "dtend":"fecha_fin"})

In [81]:
def convertir_fechaeventos(dataframe):
    for col in dataframe.filter(like="fecha", axis=1):
        dataframe[col] = pd.to_datetime(dataframe[col])
    return dataframe

In [82]:
convertir_fechaeventos(df_eventos)

id_evento                                      nombre_evento  \
0             1            25º aniversario de la revista La Fragua   
56            2           Asalto a la lectura. Tres cerditos y más   
60            3                              Atlantiques + Dahomey   
72            4             Baile de Carnaval. Concierto de Origen   
73            5         Baile de Carnaval. Concierto de Versioneta   
94            6                                    Black sad women   
118           7  Carnaval en familia. Espectáculo familiar. Car...   
121           8                               Carnaval en Matadero   
132           9                                       Century Rock   
141          10                                          Chup-Chup   
161          11                                     Circo Homónimo   
215          12                              Concurso de disfraces   
216          13         Concurso de Disfraces y Baile con Orquesta   
217          14         Concurso de Disfraces y Baile con Orquesta   
237          15                               Coro Yelena Lafargue   
247          16                       Cuatro historias de alquiler   
263          17                    De Casa de Campo a Madrid Río I   
285          18          Desfile con charanga y taller de máscaras   
305          19                                       El arca rusa   
310          20                        El carnaval de los animales   
327          21                    El Retiro a través de la música   
376          22                   Exhibición de chirigotas adultos   
377          23                Exhibición de chirigotas infantiles   
394          24  Exposición de Pintura `Paisajes´ y `Rincones d...   
398          25   Exposición de pintura: 'Evelyn contemporary art'   
427          26     Fiesta de carnaval en el Barrio del Aeropuerto   
428          27  Fiesta de carnaval en el Barro de la Alameda d...   
463          28                                    Huerto familiar   
489          29           Itinerario Ornitológico Parque del Oeste   
490          30  Itinerario Ornitológico Parque Emperatriz Marí...   
495          31  Itinerario por el Parque Forestal de Valdebeba...   
533          32                             Julieta, pero no mucho   
556          33                            La gira de rock Quijote   
599          34             Las marionetas de la Dehesa te cuentan   
620          35                         Los gigantes de la montaña   
627          36                        Los secretos de los cuentos   
628          37        Los Secretos del Capricho: público familiar   
629          38                                      Los soñadores   
649          39                                            Macbeth   
660          40  Marconi. Pasacalles, Concurso de Disfraces y O...   
682          41                                           Memories   
684          42                   Mermelhada - El Retablo (Madrid)   
706          43                                             Murdle   
732          44                             Nosotras creamos mundo   
791          45                       Rastreando la vida silvestre   
808          46  Retrato de la Mujer en Ciencia:  ilustrando la...   
826          47  San Cristóbal de los Ángeles. Concurso de Disf...   
832          48  Senda Descubre la vida silvestre del parque de...   
834          49            Senderismo al invernadero de Arganzuela   
835          50  Senderismo urbano. Emilia Pardo Bazán: mujer e...   
850          51       Sobreviure a l'incendi: El documental de ZOO   
866          52  Taller de Bancal lasaña en el Huerto Urbano Co...   
904          53  Taller de semilleros en el Huerto Urbano Comun...   
920          54                               Talleres de máscaras   
926          55  Talleres Infantiles de Carnaval. Centros Socio...   
939          56                                   Tejiendo Colores   
989          57 

In [83]:
df_eventos["codigo_postal"]= df_eventos["codigo_postal"].replace("No Disponible", None)

In [84]:
df_eventos["codigo_postal"] = df_eventos["codigo_postal"].fillna(0).astype(int)

In [85]:
df_eventos["id_evento"].duplicated().sum()

np.int64(0)

In [86]:
df_eventos["codigo_postal"]= df_eventos["codigo_postal"].replace(0, None)

* Tabla Hoteles

In [87]:
df_hoteles1 = pd.concat([dfpropio, dfcompetencia_mergeado], axis=0, ignore_index = True)

In [88]:
df_hoteles1.drop_duplicates(inplace=True)

In [89]:
df_hoteles1.columns

Index(['id_reserva', 'id_cliente', 'nombre', 'apellido', 'mail', 'competencia',
       'fecha_reserva', 'inicio_estancia', 'final_estancia', 'id_hotel',
       'precio_noche', 'nombre_hotel', 'estrellas', 'ciudad'],
      dtype='object')

In [90]:
df_hoteles = df_hoteles1[["id_hotel", "nombre_hotel", "competencia", "estrellas", "ciudad"]]

In [91]:
df_hoteles["id_ciudad"] = df_hoteles["ciudad"].map(dict(zip(df_ciudad["ciudad"], df_ciudad["id_ciudad"])))

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\3360193634.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_hoteles["id_ciudad"] = df_hoteles["ciudad"].map(dict(zip(df_ciudad["ciudad"], df_ciudad["id_ciudad"])))


In [92]:
df_hoteles.drop(columns = ["ciudad"], inplace = True)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\1614975288.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_hoteles.drop(columns = ["ciudad"], inplace = True)


In [93]:
df_hoteles["estrellas"] = df_hoteles["estrellas"].astype(float)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\1569813503.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_hoteles["estrellas"] = df_hoteles["estrellas"].astype(float)


In [94]:
df_hoteles.drop_duplicates(inplace=True)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\3065713593.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_hoteles.drop_duplicates(inplace=True)


* Tabla clientes

In [95]:
df_clientes1 = df_hoteles1[["id_cliente", "nombre", "apellido", "mail"]]

In [96]:
df_clientes1.drop_duplicates(inplace=True)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\2224594799.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clientes1.drop_duplicates(inplace=True)


* Tabla reservas

CREATE TABLE 
reservas (

    id_reserva VARCHAR(50) PRIMARY KEY,

    fecha_reserva DATE,

    inicio_estancia DATE,

    final_estancia DATE,

    precio_noche FLOAT CHECK (precio_noche >= 0),

    id_cliente VARCHAR(50) REFERENCES clientes(id_cliente) ON DELETE CASCADE,

    id_hotel INT REFERENCES hoteles(id_hotel) ON DELETE CASCADE
    
);

In [97]:
df_hoteles1.columns

Index(['id_reserva', 'id_cliente', 'nombre', 'apellido', 'mail', 'competencia',
       'fecha_reserva', 'inicio_estancia', 'final_estancia', 'id_hotel',
       'precio_noche', 'nombre_hotel', 'estrellas', 'ciudad'],
      dtype='object')

In [98]:
df_reservas = df_hoteles1[["id_reserva", "fecha_reserva", "inicio_estancia", "final_estancia", "precio_noche", "id_cliente", "id_hotel"]]

In [99]:
df_reservas["precio_noche"] = df_reservas["precio_noche"].astype(float)

C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\4290797260.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_reservas["precio_noche"] = df_reservas["precio_noche"].astype(float)


In [100]:
col_fechas = ["fecha_reserva", "inicio_estancia", "final_estancia"]
for col in col_fechas:
    df_reservas[col] = pd.to_datetime(df_reservas[col])
df_reservas.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15000 entries, 0 to 14999
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   id_reserva       15000 non-null  object        
 1   fecha_reserva    15000 non-null  datetime64[ns]
 2   inicio_estancia  15000 non-null  datetime64[ns]
 3   final_estancia   15000 non-null  datetime64[ns]
 4   precio_noche     15000 non-null  float64       
 5   id_cliente       15000 non-null  int64         
 6   id_hotel         15000 non-null  int64         
dtypes: datetime64[ns](3), float64(1), int64(2), object(1)
memory usage: 820.4+ KB


C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\2932293234.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_reservas[col] = pd.to_datetime(df_reservas[col])
C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\2932293234.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_reservas[col] = pd.to_datetime(df_reservas[col])
C:\Users\pepel\AppData\Local\Temp\ipykernel_4424\2932293234.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer

In [101]:
df_reservas.dtypes

id_reserva                 object
fecha_reserva      datetime64[ns]
inicio_estancia    datetime64[ns]
final_estancia     datetime64[ns]
precio_noche              float64
id_cliente                  int64
id_hotel                    int64
dtype: object

* Carga

In [102]:
import psycopg2

# Configurar la conexión
conn = psycopg2.connect(
    dbname="ETLPROYECTOPRUEBA",
    user="postgres",
    password="admin",
    host="localhost",
    port="5432"
)

# Crear un cursor para ejecutar comandos SQL
cur = conn.cursor()

# Verificar la conexión
cur.execute("SELECT version();")
print(cur.fetchone())

# Cerrar la conexión
cur.close()
conn.close()

('PostgreSQL 16.4, compiled by Visual C++ build 1940, 64-bit',)


In [103]:
# Reabrir la conexión
conn = psycopg2.connect(
    dbname="ETLPROYECTOPRUEBA",
    user="postgres",
    password="admin",
    host="localhost",
    port="5432"
)
cur = conn.cursor()

* ciudad

In [104]:
insert_query = """
    INSERT INTO ciudad (nombre_ciudad)
    VALUES (%s)
"""

In [105]:
data_to_insert = []
for index, row in df_ciudad.iterrows():
    data_to_insert.append([row["ciudad"]])
data_to_insert

[['Madrid']]

In [106]:
cur.executemany(insert_query, data_to_insert)
conn.commit()

* eventos

In [107]:
insert_query = """
    INSERT INTO eventos (id_evento,
    nombre_evento,
    url_evento,
    codigo_postal,
    direccion,
    horario,
    fecha_inicio,
    fecha_fin,
    organizacion,
    id_ciudad)
    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
"""

In [108]:
df_eventos["fecha_inicio"] = pd.to_datetime(df_eventos["fecha_inicio"]).dt.strftime('%Y-%m-%d')
df_eventos["fecha_fin"] = pd.to_datetime(df_eventos["fecha_fin"]).dt.strftime('%Y-%m-%d')

In [109]:
df_eventos.dtypes

id_evento         int64
nombre_evento    object
url_evento       object
horario          object
fecha_inicio     object
fecha_fin        object
codigo_postal    object
direccion        object
organizacion     object
id_ciudad         int64
dtype: object

In [110]:
data_to_insert = []
for index, row in df_eventos.iterrows():
    data_to_insert.append([row["id_evento"],
                           row["nombre_evento"],
                           row["url_evento"],
                           row["codigo_postal"],
                           row["direccion"],
                           row["horario"],
                           row["fecha_inicio"],
                           row["fecha_fin"],
                           row["organizacion"],
                           row["id_ciudad"]])
cur.executemany(insert_query, data_to_insert)
conn.commit()

UniqueViolation: llave duplicada viola restricción de unicidad «eventos_pkey»
DETAIL:  Ya existe la llave (id_evento)=(1).


In [ ]:
conn.rollback()

In [ ]:
cur.execute("SELECT nombre_ciudad, id_ciudad FROM ciudad")
# Convertimos la consulta en un diccionario
ciudad_dict = dict(cur.fetchall())
ciudad_dict

{'Madrid': 1}

In [ ]:
def insertar_datos_automatico(df, cursor, tabla):
    columnas = df.columns.tolist()  # Extraer nombres de columnas
    columnas_str = ", ".join(columnas)
    placeholders = ", ".join(["%s"] * len(columnas))  # Generar los %s dinámicamente

    # Generar la query automáticamente
    insert_query = f"""
        INSERT INTO {tabla} ({columnas_str})
        VALUES ({placeholders})
    """

    # Convertir los datos del DataFrame en una lista de listas
    data_to_insert = df.values.tolist()

    # Ejecutar la inserción
    cursor.executemany(insert_query, data_to_insert)
    conn.commit()

In [ ]:
df_reservas1 = df_hoteles1.copy()
df_reservas1["precio_noche"] = df_reservas1["precio_noche"].astype(float)
col_fechas = ["fecha_reserva", "inicio_estancia", "final_estancia"]
for col in col_fechas:
    df_reservas[col] = pd.to_datetime(df_reservas[col])

In [ ]:
df_reservas1.columns

Index(['id_reserva', 'id_cliente', 'nombre', 'apellido', 'mail', 'competencia',
       'fecha_reserva', 'inicio_estancia', 'final_estancia', 'id_hotel',
       'precio_noche', 'nombre_hotel', 'estrellas', 'ciudad'],
      dtype='object')

In [ ]:
);
CREATE TABLE reservas (
    id_reserva VARCHAR(50) PRIMARY KEY,
    fecha_reserva DATE,
    inicio_estancia DATE,
    final_estancia DATE,
    precio_noche FLOAT CHECK (precio_noche >= 0),
    id_cliente VARCHAR(50) REFERENCES clientes(id_cliente) ON DELETE CASCADE,
    id_hotel INT REFERENCES hoteles(id_hotel) ON DELETE CASCADE

In [ ]:
df_reservas2 = df_reservas1[['id_reserva', 'fecha_reserva', 'inicio_estancia', 'final_estancia',
       'precio_noche', 'mail','nombre_hotel']]

In [ ]:
cur.execute("SELECT mail, id_cliente FROM clientes")
clientes_dict = dict(cur.fetchall())

In [ ]:
cur.execute("SELECT nombre_hotel, id_hotel FROM hoteles")
hoteles_dict = dict(cur.fetchall())

In [ ]:
df_reservas2["id_cliente"] = df_reservas2["mail"].map(clientes_dict)
df_reservas2.drop(columns = ["mail"], inplace = True)
df_reservas2["id_hotel"] = df_reservas2["nombre_hotel"].map(hoteles_dict)
df_reservas2.drop(columns = ["nombre_hotel"], inplace = True)

In [ ]:
df_reservas2.columns

Index(['id_reserva', 'fecha_reserva', 'inicio_estancia', 'final_estancia',
       'precio_noche', 'id_cliente', 'id_hotel'],
      dtype='object')

In [111]:
df_hoteles1.columns

Index(['id_reserva', 'id_cliente', 'nombre', 'apellido', 'mail', 'competencia',
       'fecha_reserva', 'inicio_estancia', 'final_estancia', 'id_hotel',
       'precio_noche', 'nombre_hotel', 'estrellas', 'ciudad'],
      dtype='object')

In [112]:
df_hoteles1["id_hotel"].nunique()

29

In [120]:
cur.execute("SELECT count (hoteles.id_hotel) FROM hoteles")
bonus_1 = cur.fetchall()
bonus_1

[(29,)]

In [119]:
conn.rollback()

In [3]:
# Cargar fichero y crear copia
df = pd.read_parquet("../datos/reservas_hoteles.parquet", engine='fastparquet')
dfcopia = df.copy()

# Extraer datos API
urlapi = os.getenv("urlapi")
dfapilimpio = extraccion_api(urlapi)

# Extraer datos webscrapping
url_scrap = os.getenv("url_scrap")
dictio_scrap = {}
dfscrap = scrapear_hoteles (url_scrap, dictio_scrap)

# Elminar duplicados
dfcopia.drop_duplicates(inplace=True)

# Asignar id único a cada hotel (Estaban mal asignados)
hoteles_unicos = dfcopia.groupby('nombre_hotel')['id_hotel'].unique().reset_index()
hoteles_unicos
diccionario_hoteles = {"hotel": [], "id": []}
contador = 0
for hotel in hoteles_unicos["nombre_hotel"]:
    if hotel == "":
        pass
    else:
        diccionario_hoteles["hotel"].append(hotel)
        contador = contador + 1
        diccionario_hoteles["id"].append(contador)
df_dicthoteles = pd.DataFrame(diccionario_hoteles)
mapa_hoteles = dict(zip(df_dicthoteles["hotel"], df_dicthoteles["id"]))
dfcopia["id_hotel"] = dfcopia["nombre_hotel"].map(mapa_hoteles).fillna(df["id_hotel"])
dfcopia["id_hotel"] = dfcopia["id_hotel"].astype(int)

# Cambiar ID cliente (había mas IDs que clientes)
lista_mails = dfcopia["mail"].unique().tolist()
lista_idmails = []
contador = 0
for mail in lista_mails:
    contador = contador + 1
    lista_idmails.append(contador)
diccionario_mails = dict(zip(lista_mails, lista_idmails))
dfcopia["id_cliente"] = dfcopia["mail"].map(diccionario_mails)
dfcopia["id_cliente"] = dfcopia["id_cliente"].astype(int)

# Cambiar nulos inicio y final de estancia (siempre es la misma fecha)
dfcopia["inicio_estancia"] = dfcopia["inicio_estancia"].fillna("2025-03-01")
dfcopia["final_estancia"] = dfcopia["final_estancia"].fillna("2025-03-02")

# Cambiar precio noche de los hoteles no competencia por media de precios del hotel
medias = dfcopia.groupby("id_hotel")["precio_noche"].mean().round(2)
medias = pd.DataFrame(medias).reset_index()
diccionario_medias = dict(zip(medias["id_hotel"], medias["precio_noche"]))
dfcopia['precio_noche'] = dfcopia['precio_noche'].fillna(dfcopia['id_hotel'].map(diccionario_medias))

# Rellenar columna ciudad con Madrid (siempre es Madrid)
dfcopia["ciudad"] = "Madrid"

# Crear df con solo hoteles competencia y df solo hoteles propios
dfpropio = dfcopia[dfcopia["competencia"] == False]
dfcompetencia = dfcopia[dfcopia["competencia"] == True]

# Modificar las valoraciones de los hoteles propios (tienen distintas valoraciones y se rellena con la media)
medias_valoraciones = dfpropio.groupby("id_hotel")["estrellas"].mean().round(2).reset_index()
diccionario_valoraciones = dict(zip(medias_valoraciones["id_hotel"], medias_valoraciones["estrellas"]))
dfpropio["estrellas"] = dfpropio["id_hotel"].map(diccionario_valoraciones)

# Unir dfcompetencia con el df webscrapping
dictio_mergeo = dict(zip(dfscrap["nombre_hotel"], dfcompetencia["id_hotel"].unique().tolist()))
dfscrap["id_hotel"] = dfscrap["nombre_hotel"].map(dictio_mergeo)
dfcompetencia_mergeado = dfcompetencia.merge(dfscrap, on="id_hotel")
dfcompetencia_mergeado["fecha_reserva"] = dfcompetencia_mergeado["fecha"]
dfcompetencia_mergeado["precio_noche"] = dfcompetencia_mergeado["precio"]
dfcompetencia_mergeado["nombre_hotel_x"] = dfcompetencia_mergeado["nombre_hotel_y"]
dfcompetencia_mergeado = dfcompetencia_mergeado.drop(columns= ["nombre_hotel_y", "precio","fecha", "estrellas"])
dfcompetencia_mergeado = dfcompetencia_mergeado.rename(columns={"nombre_hotel_x":"nombre_hotel"})

# Limpieza fichero API
convertir_fecha(dfapilimpio)
dfapilimpio1 = dfapilimpio[(dfapilimpio["dtstart"] == "2025-03-01") | (dfapilimpio["dtend"] == "2025-03-02")]
dfapilimpio1["codigo-postal"] = dfapilimpio1["address"].apply(lambda x: x.get("area", {}).get("postal-code") if pd.notna(x) else None)
dfapilimpio1["direccion"] = dfapilimpio1["address"].apply(lambda x: x.get("area", {}).get("street-address") if pd.notna(x) else None)
dfapilimpio1["organizacion"] = dfapilimpio1["organization"].apply(lambda x: x.get("organization-name", {})if pd.notna(x) else None)
dfapilimpio1 = dfapilimpio1.drop(columns = ["address", "organization"], axis = 1)
dfapilimpio1["time"] = dfapilimpio1["time"].replace('', None)

# Crear tabla unida
df_mergeado = pd.concat([dfpropio, dfcompetencia_mergeado], axis=0, ignore_index = True)

# Configurar la conexión
dbname = os.getenv("dbname")
user = os.getenv("user")
password = os.getenv("password")
host = os.getenv("host")
port = os.getenv("port")
[conn, cur] = conexion_postgres(dbname, user, password, host, port)

{'@context': {'c': 'http://www.w3.org/2002/12/cal#', 'dcterms': 'http://purl.org/dc/terms/', 'geo': 'http://www.w3.org/2003/01/geo/wgs84_pos#', 'loc': 'http://purl.org/ctic/infraestructuras/localizacion#', 'org': 'http://purl.org/ctic/infraestructuras/organizacion#', 'vcard': 'http://www.w3.org/2006/vcard/ns#', 'schema': 'https://schema.org/', 'title': 'vcard:fn', 'id': 'dcterms:identifier', 'relation': 'dcterms:relation', 'references': 'dcterms:references', 'address': 'vcard:adr', 'area': 'loc:barrio', 'district': 'loc:distrito', 'locality': 'vcard:locality', 'postal-code': 'vcard:postal-code', 'street-address': 'vcard:street-address', 'location': 'vcard:geo', 'latitude': 'geo:lat', 'longitude': 'geo:long', 'organization': 'vcard:org', 'organization-desc': 'dcterms:description', 'accesibility': 'org:accesibilidad', 'services': 'org:servicios', 'schedule': 'org:horario', 'organization-name': 'vcard:organization-name', 'description': 'c:summary', 'link': 'c:url', 'uid': 'c:uid', 'dtstar

C:\Users\pepel\AppData\Local\Temp\ipykernel_13940\1771352822.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfpropio["estrellas"] = dfpropio["id_hotel"].map(diccionario_valoraciones)
C:\Users\pepel\AppData\Local\Temp\ipykernel_13940\1771352822.py:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfapilimpio1["codigo-postal"] = dfapilimpio1["address"].apply(lambda x: x.get("area", {}).get("postal-code") if pd.notna(x) else None)
C:\Users\pepel\AppData\Local\Temp\ipykernel_13940\1771352822.py:81: Settin

In [9]:
cur.execute("SELECT count (hoteles.id_hotel) FROM hoteles")
bonus_1 = cur.fetchone()
bonus_1

(29,)

In [8]:
conn.rollback()